1. Download

In [ ]:
#pip install opencv-python matplotlib tensorflow mediapipe scikit-learn

2. Import

In [ ]:
import cv2
import numpy as np
import os
from matplotlib import pyplot as plt    # MIGHT REMOVE
import time                             # MIGHT REMOVE
import mediapipe as mp
import tensorflow as tf

from sklearn.model_selection import train_test_split
from tensorflow.keras.utils import to_categorical

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.callbacks import TensorBoard # MIGHT REMOVE

mp_pose = mp.solutions.pose
mp_draw = mp.solutions.drawing_utils

3. Functions

In [ ]:
# Mediapipe Detection Function
def mediapipe_detection(image, model):
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)  # Color Conversion BGR to RGB
    image.flags.writeable = False                   # Non-writeable
    results = model.process(image)                  # Make Prediction
    image.flags.writeable = True                    # Writeable
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)  # Color Conversion RGB back to BGR
    return image, results

In [ ]:
# Mediapipe Draw Function
def draw_styled_landmarks(image, results):
    mp_draw.draw_landmarks(image, results.pose_landmarks, mp_pose.POSE_CONNECTIONS,                     # Draw Face
                              mp_draw.DrawingSpec(color=(255,255,255), thickness=1, circle_radius=1),   # Face Dot Color
                              mp_draw.DrawingSpec(color=(240,19,255), thickness=1, circle_radius=1),    # Face Line Color
                              )

In [ ]:
# Extract Keypoints Function
def extract_keypoints(results):
    pose = np.array([[res.x, res.y, res.z] for res in results.pose_landmarks.landmark]).flatten() if results.pose_landmarks else np.zeros(33*3)
    return pose

TEST Pose Detection

In [ ]:
cap = cv2.VideoCapture(0)
# Set Mediapipe Model
with mp_pose.Pose(min_detection_confidence=0.8, min_tracking_confidence=0.8) as pose_model:
    while cap.isOpened():
        
        # Read Feed
        ret, frame = cap.read()
        
        # Make Detections
        image, results = mediapipe_detection(frame, pose_model)
        print(results)
        
        # Draw Landmarks
        draw_styled_landmarks(image, results)

        # Show Feed
        cv2.imshow('OpenCV Feed', image)

        # Break Loop
        if cv2.waitKey(10) & 0xFF == ord('q'):
            break

    # If Broken
    cap.release()
    cv2.destroyAllWindows()

4. Training

In [110]:
# Path for stored data
DATA_PATH = os.path.join('MP_DATA30n+')

# Actions to detect
#actions = np.array(['deadlift-s', 'deadlift-c', 'squat-s', 'squat-c']) # S = Starting Point, C = Contraction Point
actions = np.array(['unknown', 'deadlift-s', 'deadlift-c', 'squat-s', 'squat-c']) # S = Starting Point, C = Contraction Point

sequence_length = 30

In [ ]:
# Create Directory
for action in actions: 
    os.makedirs(os.path.join(DATA_PATH, action))

In [ ]:
cap = cv2.VideoCapture(0)
tempPath = 'ExtraData'

with mp_pose.Pose(min_detection_confidence=0.8, min_tracking_confidence=0.8) as pose_model:
    while cap.isOpened():
        
        ret, frame = cap.read()
        image, results = mediapipe_detection(frame, pose_model)
        draw_styled_landmarks(image, results)

        cv2.putText(image, 'Collectiong frames for {}'.format(action), (0,12),
                                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,0,255), 1, cv2.LINE_AA)

        cv2.imshow('Data Capture', image)

        key = cv2.waitKey(10) & 0xFF
        if key == ord('1'):
            action = 'nothing'
        elif key == ord('2'):
            if action == actions[1]:
                action = actions[2]
            else:
                action = actions[1]
        elif key == ord('3'):
            if action == actions[3]:
                action = actions[4]
            else:
                action = actions[3]
        elif key == ord(' '):
            # Make New Directory
            name = str(len(os.listdir(os.path.join(tempPath, action))))
            os.makedirs(os.path.join(tempPath, action, name))

            for i in range(sequence_length):
                ret, frame = cap.read()
                image, results = mediapipe_detection(frame, pose_model)
                print(results)
                draw_styled_landmarks(image, results)
                cv2.imshow('Data Capture', image)
                npy_path = os.path.join(tempPath, action, name, str(i))
                keypoints = extract_keypoints(results)
                np.save(npy_path, keypoints)
        elif key == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

In [ ]:
cap.release()
cv2.destroyAllWindows()

In [111]:
label_map = {label:num for num, label in enumerate(actions)}

In [112]:
label_map

{'unknown': 0, 'deadlift-s': 1, 'deadlift-c': 2, 'squat-s': 3, 'squat-c': 4}

In [114]:
no_sequences = 30 # Number of recordings made for each action

sequences, labels = [], []
for action in actions:
    for sequence in range(no_sequences):
        window = []
        for frame_num in range(sequence_length):
            res = np.load(os.path.join(DATA_PATH, action, str(sequence), "{}.npy".format(frame_num)))
            window.append(res)
        sequences.append(window)
        labels.append(label_map[action])

In [115]:
# !!! ONLY FOR LABELING WITH DIFFERENT AMOUNTS OF DATA !!!

no_sequences = 30 # Number of recordings made for each action

sequences, labels = [], []
for action in actions:
    if action == 'unknown':
        no_sequences = 45
    else:
        no_sequences = 30
    for sequence in range(no_sequences):
        window = []
        for frame_num in range(sequence_length):
            res = np.load(os.path.join(DATA_PATH, action, str(sequence), "{}.npy".format(frame_num)))
            window.append(res)
        sequences.append(window)
        labels.append(label_map[action])

In [116]:
labels

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4,
 4]

In [117]:
sequences

[[array([ 0.4752574 ,  0.09410358, -0.23529606,  0.48065096,  0.07639889,
         -0.20195322,  0.48520699,  0.07664154, -0.20192623,  0.48953375,
          0.07678376, -0.20194964,  0.46496502,  0.0756029 , -0.22576901,
          0.45866027,  0.07523586, -0.22571945,  0.45429271,  0.07466403,
         -0.22570786,  0.49139547,  0.08395081,  0.00193574,  0.44576851,
          0.08199228, -0.09964559,  0.48407382,  0.11761776, -0.15433905,
          0.46395555,  0.11732872, -0.18701369,  0.50744379,  0.21357939,
          0.16454396,  0.42466378,  0.18257816, -0.14742292,  0.53925228,
          0.33782271,  0.09316565,  0.50809801,  0.30027586, -0.21765427,
          0.62091905,  0.31535691, -0.21812864,  0.6234563 ,  0.29840869,
         -0.15493181,  0.64773488,  0.30877408, -0.28285605,  0.64962077,
          0.29846922, -0.19021584,  0.6518181 ,  0.29537743, -0.31513578,
          0.65221179,  0.28326988, -0.200598  ,  0.64216715,  0.29769817,
         -0.24469447,  0.64296925,  0.

In [129]:
x = np.array(sequences)

In [130]:
y = to_categorical(labels).astype(int)

In [131]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size = 0.05)

In [132]:
log_dir = os.path.join('logs')
tb_callback = TensorBoard(log_dir=log_dir)

In [ ]:
model = Sequential()
model.add(LSTM(64, return_sequences=True, activation='relu', input_shape=(30,99)))    # 10/30 = frames
model.add(LSTM(128, return_sequences=True, activation='relu'))
model.add(LSTM(64, return_sequences=False, activation='relu'))
model.add(Dense(64, activation='relu'))
model.add(Dense(32, activation='relu'))
model.add(Dense(actions.shape[0], activation='softmax'))

In [ ]:
model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['categorical_accuracy']) # Look up optimizer

In [ ]:
model.fit(x_train, y_train, epochs=70, callbacks=[tb_callback]) # Be vary of the epochs, potentially stop early

In [ ]:
del model

In [ ]:
model.save('exercise30n+.keras')
model.save('exercise30n+.h5')

In [122]:
model = tf.keras.models.load_model('Models\\exercise30n+.keras')

5. Test Model

In [133]:
from sklearn.metrics import multilabel_confusion_matrix, accuracy_score

In [ ]:
# Look in other project when ready to test model

In [134]:
testRes = model.predict(x_test)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step


In [135]:
testRes

array([[9.82840538e-01, 6.48324331e-03, 9.84072965e-03, 6.05445763e-04,
        2.30148362e-04],
       [3.05144757e-01, 9.30708647e-02, 7.97793493e-02, 3.15219849e-01,
        2.06785247e-01],
       [1.33413270e-01, 3.78236029e-04, 5.88838535e-04, 8.59923840e-01,
        5.69575140e-03],
       [1.71797856e-05, 9.99982715e-01, 9.80095507e-08, 1.03506285e-26,
        9.31261155e-33],
       [7.32444605e-05, 2.97725154e-03, 9.96949613e-01, 0.00000000e+00,
        0.00000000e+00],
       [1.56720523e-02, 8.12051439e-06, 1.32052301e-05, 9.42136049e-01,
        4.21705469e-02],
       [4.66604121e-02, 1.13045309e-04, 1.68109007e-04, 9.50081408e-01,
        2.97704223e-03],
       [1.53624185e-03, 9.98325050e-01, 1.38741612e-04, 1.18146673e-10,
        3.84855396e-13],
       [1.08246008e-04, 9.99891758e-01, 2.43774889e-09, 1.94595735e-24,
        6.19198777e-30]], dtype=float32)

In [136]:
np.sum(testRes[3])

1.0

In [137]:
actions[np.argmax((testRes[3]))]

'deadlift-s'

In [138]:
actions[np.argmax(y_test[3])]

'deadlift-s'

In [139]:
yhat = model.predict(x_train)

5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step  


In [140]:
ytrue = np.argmax(y_train, axis=1).tolist()
yhat = np.argmax(yhat, axis=1).tolist()

In [141]:
multilabel_confusion_matrix(ytrue, yhat)

array([[[114,   0],
        [  2,  40]],

       [[128,   1],
        [  1,  26]],

       [[126,   1],
        [  0,  29]],

       [[127,   1],
        [  1,  27]],

       [[125,   1],
        [  0,  30]]], dtype=int64)

6. Live Predictions

In [142]:
sequence = []
res = [0]

cap = cv2.VideoCapture(0)
with mp_pose.Pose(min_detection_confidence=0.8, min_tracking_confidence=0.8) as pose_model:
    while cap.isOpened():
        ret, frame = cap.read()
        image, results = mediapipe_detection(frame, pose_model)
        draw_styled_landmarks(image, results)

        keypoints = extract_keypoints(results)
        sequence.append(keypoints)
        sequence = sequence[-30:]
        currentFrame = len(sequence)

        if len(sequence) == 30:
            res = model.predict(np.expand_dims(sequence, axis=0))[0]
            sequence = sequence[-20:] # Delay

        currentConf =  res[np.argmax(res)]
        currentRes = actions[np.argmax(res)]

        if currentConf >= 0.7:
            cv2.putText(image, 'Prediction: {}'.format(currentRes), (0,34),
                        cv2.FONT_HERSHEY_SIMPLEX, 1.5, (0,0,0), 2, cv2.LINE_AA)
            cv2.putText(image, 'Confidence: {}'.format(currentConf), (0,50),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,0,0), 1, cv2.LINE_AA)
            cv2.putText(image, 'Frames: {}'.format(currentFrame), (0,70), 
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,0,0), 1, cv2.LINE_AA)
        elif currentConf >= 0.5:
            cv2.putText(image, 'Prediction: {}'.format(currentRes), (0,34),
                        cv2.FONT_HERSHEY_SIMPLEX, 1.5, (0,165,255), 2, cv2.LINE_AA)
            cv2.putText(image, 'Confidence: {}'.format(currentConf), (0,50),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,165,255), 1, cv2.LINE_AA)
            cv2.putText(image, 'Frames: {}'.format(currentFrame), (0,70), 
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,165,255), 1, cv2.LINE_AA)
        else:
            cv2.putText(image, 'Prediction: {}'.format(currentRes), (0,34),
                        cv2.FONT_HERSHEY_SIMPLEX, 1.5, (0,0,255), 2, cv2.LINE_AA)
            cv2.putText(image, 'Confidence: {}'.format(currentConf), (0,50),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,0,255), 1, cv2.LINE_AA)
            cv2.putText(image, 'Frames: {}'.format(currentFrame), (0,70), 
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,0,255), 1, cv2.LINE_AA)

        cv2.imshow('Prediction Feed', image)

        key = cv2.waitKey(10) & 0xFF
        if key == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step


In [ ]:
cap.release()
cv2.destroyAllWindows()